### Notebook to run initial analyses on the dynamics of KF aggregate formation
1) Generate reference sphere mesh 
2) Look at deep cell density fluctuations over time: how early is aggregate position apparent?
3) Pull basic stats: entropy, velocity, cell number

In [1]:
import os
import pandas as pd
import numpy as np
from src.utilities.shape_utils import plot_mesh
from scipy.spatial import KDTree
import plotly.express as px
import trimesh

# Load test dataset that used Kikume NLS marker
root = "E:\\Nick\\Cole Trapnell's Lab Dropbox\\Nick Lammers\\Nick\\killi_tracker\\"
experiment_date = "20240611_NLS-Kikume_24hpf_side2"
config_name = "tracking_jordao_20240918.txt"
model ="LCP-Multiset-v1"
tracking_folder = config_name.replace(".txt", "")
tracking_folder = tracking_folder.replace(".toml", "")

well_num = 0
start_i = 0
stop_i = 1600

suffix = ""

# get path to metadata
metadata_path = os.path.join(root, "metadata", "tracking")

# set output path for tracking results
project_path = os.path.join(root, "tracking", experiment_date,  tracking_folder, f"well{well_num:04}" + suffix, "")
project_sub_path = os.path.join(project_path, f"track_{start_i:04}" + f"_{stop_i:04}" + suffix, "")

# load the tracks 
tracks_df = pd.read_csv(os.path.join(project_sub_path, "tracks01.csv"))
tracks_df.head()

track_id  t    z     y      x       id  parent_track_id  parent_id  \
0         1  0  5.0  58.0  441.0  1000001               -1         -1   
1         1  1  5.0  58.0  441.0  2000001               -1    1000001   
2         1  2  5.0  57.0  441.0  3000001               -1    2000001   
3         1  3  5.0  57.0  441.0  4000001               -1    3000001   
4         1  4  5.0  56.0  440.0  5000001               -1    4000001   

     volume  gmm_label  gmm0_prob  gmm1_prob  gmm_logL  
0  3324.375        0.0   0.633889   0.366111 -2.073905  
1  3587.625        0.0   0.633889   0.366111 -2.073905  
2  3439.125        0.0   0.633889   0.366111 -2.073905  
3  3206.250        0.0   0.633889   0.366111 -2.073905  
4  3196.125        0.0   0.633889   0.366111 -2.073905

In [2]:
# if on mac
# tracks_df = pd.read_csv("/Users/nick/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/killi_temp/tracks01.csv")
# tracks_df.head()

### Filter for deep cells only
This process is kind of crude for mRNA-injection, but should be much more robust for transgenic embryos

In [3]:
# calculate average velocity and volume
tracks_df_v = tracks_df.copy()
tracks_df_v[["dx", "dy", "dz"]] = tracks_df_v.loc[:, ["track_id", "x", "y", "z"]].groupby(["track_id"]).diff()
tracks_df_v["v"] = np.sqrt(tracks_df_v["dx"]**2 + tracks_df_v["dy"]**2 + tracks_df_v["dz"]**2)
tracks_df_v = tracks_df_v.loc[:, ["track_id", "v"]].groupby(["track_id"]).mean().reset_index()

tracks_df = tracks_df.merge(tracks_df_v, how="left", on="track_id")

tracks_df.head()

track_id  t    z     y      x       id  parent_track_id  parent_id  \
0         1  0  5.0  58.0  441.0  1000001               -1         -1   
1         1  1  5.0  58.0  441.0  2000001               -1    1000001   
2         1  2  5.0  57.0  441.0  3000001               -1    2000001   
3         1  3  5.0  57.0  441.0  4000001               -1    3000001   
4         1  4  5.0  56.0  440.0  5000001               -1    4000001   

     volume  gmm_label  gmm0_prob  gmm1_prob  gmm_logL         v  
0  3324.375        0.0   0.633889   0.366111 -2.073905  0.812908  
1  3587.625        0.0   0.633889   0.366111 -2.073905  0.812908  
2  3439.125        0.0   0.633889   0.366111 -2.073905  0.812908  
3  3206.250        0.0   0.633889   0.366111 -2.073905  0.812908  
4  3196.125        0.0   0.633889   0.366111 -2.073905  0.812908

In [4]:
gmm_filter = tracks_df["gmm0_prob"] >= 0.5 # use probs from GMM
vel_filter0 = tracks_df["v"] >= 2 # add fast-but-large nuclei. In practice most of these look like deep cells
vel_filter1 = tracks_df["v"] <= 0.2 # remove these

deep_filter = (gmm_filter | vel_filter0) & (~vel_filter1)

deep_tracks_df = tracks_df.loc[deep_filter, :].copy()
deep_tracks_df.shape

(468829, 14)

### First pass: use NN neighbor distances to estimate density

In [93]:
t = 500
kn = 70
time_filter = (deep_tracks_df["t"]<=t+5) & (tracks_df["t"]>=t-5)
deep_tracks_df_t = deep_tracks_df.loc[time_filter, :]
points = deep_tracks_df_t.loc[:, ["x", "y", "z"]].to_numpy()

# Initialize the KDTree
tree = KDTree(points)
distances, indices = tree.query(points, k=kn)
dist_mean = np.mean(distances[:, 1:], axis=1)

# tracks_reflected = 
fig = px.scatter_3d(deep_tracks_df_t, x="x", y="y", z="z", color=100*dist_mean**-2, range_color=[0, 0.5],)

fig.show()

### Can we do better? Let's calculate a reference sphere
If the embryo is relatively stable, then we can use a single sphere throughout. Let's see if that works

In [67]:
import plotly.graph_objects as go
from src.utilities.functions import sphereFit

# filter for points later than epibole but beforeserious aggregation
min_sphere_time = 900
max_sphere_time = 1300

time_filter = (deep_tracks_df["t"]<=max_sphere_time) & (tracks_df["t"]>=min_sphere_time)
deep_tracks_df_t = deep_tracks_df.loc[time_filter, :]
sphere_points = deep_tracks_df_t.loc[:, ["x", "y", "z"]].to_numpy()

# fit a sphere to the points
r, C = sphereFit(sphere_points[:, 0], sphere_points[:, 1], sphere_points[:, 2])
center = np.asarray(C[:3].ravel())

# initialize a mesh unit sphere
sphere_mesh_raw = trimesh.creation.icosphere(subdivisions=2, radius=1.0)

verts = np.asarray(sphere_mesh_raw.vertices.copy())
verts = verts * r
verts = verts + center[None, :]

sphere_mesh = sphere_mesh_raw.copy()
sphere_mesh.vertices = verts

In [68]:
from plotly.subplots import make_subplots

times_to_plot = [0, 700, 1400] 

points_list = []
for time in times_to_plot:
    time_filter = deep_tracks_df["t"]==time
    points = deep_tracks_df.loc[time_filter, ["x", "y", "z"]].to_numpy()
    points_list.append(points)

# check at different tim points
_, sphere_grid, sphere_lines = plot_mesh(sphere_mesh, surf_alpha=0.75)

# Create a 1x3 grid of 3D subplots
fig = make_subplots(
    rows=1, cols=3,
    specs=[[{"type": "surface"}, {"type": "surface"}, {"type": "surface"}]],
    subplot_titles=[f"time {times_to_plot[0]}", f"time {times_to_plot[1]}", f"time {times_to_plot[0]}"]
)

# Add the same surface to each subplot
for col in range(1, 4):
    fig.add_trace(sphere_grid, row=1, col=col)

# Add scatter points to each subplot
for i, points in enumerate(points_list):
    scatter_plot = go.Scatter3d(
        x=points[:, 0],
        y=points[:, 1],
        z=points[:, 2],
        mode="markers",
        marker=dict(size=4),
        name=f"Scatter {i + 1}"
    )
    fig.add_trace(scatter_plot, row=1, col=i + 1)

# Update layout
fig.update_layout(
    height=600,  # Overall figure height
    width=1800,  # Overall figure width
    title_text="3D Subplots with Different Scatters"
)

fig.show()

Not perfect, but good enough for government work

### Get counts of cells per face over time

In [66]:
from tqdm import tqdm

t_start = 0
t_stop = 1600
time_vec = np.arange(t_start, t_stop)
n_times = len(time_vec)

# generate face- and vertex-based data frames to store counts
n_faces = len(sphere_mesh.faces)
n_vertices = len(sphere_mesh.vertices)

f_cols = [f"face{f:04}" for f in range(n_faces)]
v_cols = [f"vert{v:04}" for v in range(n_vertices)]

face_df = pd.DataFrame(time_vec, columns=["time"])
face_df.loc[:, f_cols] = np.zeros((n_times, n_faces))
vert_df = pd.DataFrame(time_vec, columns=["time"])
vert_df.loc[:, v_cols] = np.zeros((n_times, n_vertices))

# iterate through time points
for time in tqdm(time_vec):
    
    time_filter = deep_tracks_df["t"]==time
    points = deep_tracks_df.loc[time_filter, ["x", "y", "z"]].to_numpy()
#     track_ids = deep_tracks_df.loc[time_filter, ["x", "y", "z"]].to_numpy()
    # Find the closest faces for each point
    closest_points, distances, face_indices = sphere_mesh.nearest.on_surface(points)

    # add to track df
    deep_tracks_df.loc[time_filter, "mesh_face_id"] = face_indices
    
    # Count the number of points associated with each face
    face_counts = np.bincount(face_indices, minlength=len(sphere_mesh.faces))
    
    # store
    face_df.loc[face_df["time"]==time, f_cols] = face_counts
    
    # calculate vertex averages
    # Initialize vertex intensity array
    vertex_intensity = np.zeros(n_vertices)
    vertex_counts = np.zeros(n_vertices)  # Track contributions per vertex

    # Map face values to vertex intensity
    for i, face in enumerate(sphere_mesh.faces):
        for vertex in face:
            vertex_intensity[vertex] += face_counts[i]  # Sum face values for each vertex
            vertex_counts[vertex] += 1  # Track how many times each vertex is used

    # Average intensity per vertex
    vertex_intensity /= vertex_counts
    vert_df.loc[vert_df["time"]==time, v_cols] = vertex_intensity

  0%|          | 8/1600 [00:28<1:35:02,  3.58s/it]


KeyboardInterrupt: 

In [29]:
face_df.to_csv(os.path.join(project_sub_path, "face_cell_counts.csv"), index=False)
vert_df.to_csv(os.path.join(project_sub_path, "vert_cell_counts.csv"), index=False)

In [69]:
face_df = pd.read_csv(os.path.join(project_sub_path, "face_cell_counts.csv"))
vert_df = pd.read_csv(os.path.join(project_sub_path, "vert_cell_counts.csv"))

# generate face- and vertex-based data frames to store counts
n_faces = len(sphere_mesh.faces)
n_vertices = len(sphere_mesh.vertices)

f_cols = [f"face{f:04}" for f in range(n_faces)]
v_cols = [f"face{v:04}" for v in range(n_vertices)]

face_df.head()

time  face0000  face0001  face0002  face0003  face0004  face0005  face0006  \
0     0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1     1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2     2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
3     3       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
4     4       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   face0007  face0008  ...  face0310  face0311  face0312  face0313  face0314  \
0       0.0       0.0  ...       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0  ...       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0  ...       0.0       0.0       0.0       0.0       0.0   
3       0.0       0.0  ...       0.0       0.0       0.0       0.0       0.0   
4       0.0       0.0  ...       0.0       0.0       0.0       0.0       0.0   

   face0315  face0316  face0317  face0318  face0319  
0       0.0       0.0       0.0       0.0       0.0  
1       0.0       0.0       0.0       0.0       0.0  
2       0.0       0.0       0.0       0.0       0.0  
3       0.0       0.0       0.0       0.0       0.0  
4       0.0       0.0       0.0       0.0       0.0  

[5 rows x 321 columns]

In [95]:
vert_df_avg = vert_df.copy()
vert_df_avg[v_cols] = vert_df_avg[v_cols].rolling(window=5, center=True, min_periods=1).mean()
vert_df_avg.head()
vert_nz_indices = np.where(np.max(vert_df_avg[v_cols].to_numpy(), axis=0)>0)[0]
vert_nz_cols = [v_cols[z] for z in range(len(v_cols)) if z in vert_nz_indices]

face_df_avg = face_df.copy()
face_df_avg[f_cols] = face_df_avg[f_cols].rolling(window=5, center=True, min_periods=1).mean()
face_nz_indices = np.where(np.max(face_df_avg[v_cols].to_numpy(), axis=0)>0)[0]
face_nz_cols = [f_cols[z] for z in range(len(f_cols)) if z in face_nz_indices]

In [117]:
plot_time = 900

# # generate face- and vertex-based data frames to store counts
# n_faces = len(sphere_mesh.faces)
# n_vertices = len(sphere_mesh.vertices)


# time_filter = deep_tracks_df["t"]==plot_time
# points = deep_tracks_df.loc[time_filter, ["x", "y", "z"]].to_numpy()
# #     track_ids = deep_tracks_df.loc[time_filter, ["x", "y", "z"]].to_numpy()
# # Find the closest faces for each point
# closest_points, distances, face_indices = sphere_mesh.nearest.on_surface(points)

# # add to track df
# deep_tracks_df.loc[time_filter, "mesh_face_id"] = face_indices

# # Count the number of points associated with each face
# face_counts = np.bincount(face_indices, minlength=len(sphere_mesh.faces))

# # store
# #     face_df.loc[face_df["time"]==time, f_cols] = face_counts

# # calculate vertex averages
# # Initialize vertex intensity array
# vertex_intensity = np.zeros(n_vertices)
# vertex_counts = np.zeros(n_vertices)  # Track contributions per vertex

# # Map face values to vertex intensity
# for i, face in enumerate(sphere_mesh.faces):
#     for vertex in face:
#         vertex_intensity[vertex] += face_counts[i]  # Sum face values for each vertex
#         vertex_counts[vertex] += 1  # Track how many times each vertex is used

# # Average intensity per vertex
# vertex_intensity /= vertex_counts
# #     vert_df.loc[vert_df["time"]==time, v_cols] = vertex_intensity
    
vert_i = vert_df_avg.loc[vert_df_avg["time"]==plot_time, v_cols].to_numpy().ravel()
i_avg = np.mean(vert_i[nz_indices])

vi_plot = vert_i - i_avg
vi_plot[~np.isin(np.arange(n_vertices), nz_indices)] = np.nan
# Plot the mesh with colored faces
mesh_to_plot = sphere_mesh.copy()
mesh_to_plot.vertices = mesh_to_plot.vertices[:, ::-1]
fig = go.Figure() 
_, lines, mesh = plot_mesh(mesh_to_plot, surf_alpha=1)

# mesh.intensity = vert_i
fig.add_trace(mesh)

fig.data[0].update(
    intensity=vi_plot,  # Replace with your vertex intensity values
#     cmin=0,  # Optional: set the minimum intensity value
#     cmax=10   # Optional: set the maximum intensity value
)

# Adjust the view angle (camera position and orientation)
fig.update_layout(
    scene=dict(
        camera=dict(
            eye=dict(x=2, y=0, z=0.5),  # Position the camera
            up=dict(x=0, y=0, z=1),     # Define the "up" direction
#             center=dict(x=0, y=0, z=0)  # Focal point of the camera
        ),
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    )
)

# fig.add_trace(lines)
fig.show()

In [225]:
plot_time = 1450

# Prepare data for Plotly
vertices = sphere_mesh.vertices
faces = sphere_mesh.faces

# Intensity values for each face
face_intensity_array = face_df_avg.loc[:, f_cols].to_numpy()
face_i_norm = face_intensity_array - np.mean(face_intensity_array[:, face_nz_indices], axis=1)[:, None]
face_i_norm /= np.amax(face_i_norm[:, face_nz_indices])

face_i = face_i_norm[(face_df_avg["time"]==plot_time).to_numpy(), :].ravel()

# Duplicate vertices to make each face unique
x_faces = []
y_faces = []
z_faces = []
intensity_faces = []

for face, intensity in zip(faces, face_i):
    for vertex_idx in face:  # Add each vertex of the face
        x_faces.append(vertices[vertex_idx][0])
        y_faces.append(vertices[vertex_idx][1])
        z_faces.append(vertices[vertex_idx][2])
    intensity_faces.extend([intensity] * 3)   # Same intensity for all vertices of the face

# Build new indices for the triangular faces
n_faces = len(faces)
i = [3 * j for j in range(n_faces)]
j = [3 * j + 1 for j in range(n_faces)]
k = [3 * j + 2 for j in range(n_faces)]
# Create the Plotly Mesh3d plot
fig = go.Figure(data=[go.Mesh3d(
    x=x_faces,
    y=y_faces,
    z=z_faces,
    i=i,
    j=j,
    k=k,
    intensity=intensity_faces,
    colorbar_title="Face Intensity",
    flatshading=True
)])

fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    )
)

fig.show()

In [226]:
import flowshape as fs
import igl
import scipy as sp

l_max = 7

v, f = sphere_mesh.vertices.copy(), sphere_mesh.faces.copy()
# this utility does the above steps + SH decomposition
# Here, using maximum degree 24

v_sphere = fs.sphere_map(v, f)

# rho = curvature_function(v, v_sphere, f)

v_bary = igl.barycenter(v_sphere, f)
v_bary = fs.project_sphere(v_bary)
W = 0.5 * igl.doublearea(v_sphere, f)
W = sp.sparse.diags(W)
weights, Y_mat = fs.IRF_scalar(face_i, v_bary, W, max_degree=l_max)

i_recon = Y_mat.dot(weights)

# Duplicate vertices to make each face unique
x_faces = []
y_faces = []
z_faces = []
intensity_faces_recon = []

for face, intensity in zip(faces, i_recon):
    for vertex_idx in face:  # Add each vertex of the face
        x_faces.append(vertices[vertex_idx][0])
        y_faces.append(vertices[vertex_idx][1])
        z_faces.append(vertices[vertex_idx][2])
    intensity_faces_recon.extend([intensity] * 3)   # Same intensity for all vertices of the face
    
# Create the Plotly Mesh3d plot
fig = go.Figure(data=[go.Mesh3d(
    x=x_faces,
    y=y_faces,
    z=z_faces,
    i=i,
    j=j,
    k=k,
    intensity=intensity_faces_recon,
    colorbar_title="Face Intensity",
    flatshading=True
)])

fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    )
)

fig.show()

In [220]:
coeffs = weights.copy()
# l_max = 7

# Create a spherical grid
theta = np.linspace(0, np.pi, 100)  # Latitude
phi = np.linspace(0, 2 * np.pi, 200)  # Longitude
theta, phi = np.meshgrid(theta, phi)

# Evaluate the spherical harmonics
def evaluate_spherical_harmonics(coeffs, l_max, theta, phi):
    """Evaluate the scalar function from spherical harmonics coefficients."""
    scalar_field = np.zeros_like(theta)
    index = 0
    for l in range(l_max):
        for m in range(-l, l + 1):
            Y_lm = sp.special.sph_harm(m, l, phi, theta)  # m, l, phi (longitude), theta (colatitude)
            scalar_field += coeffs[index] * Y_lm.real  # Add real part of spherical harmonics
            index += 1
    return scalar_field

scalar_field = evaluate_spherical_harmonics(coefficients, l_max, theta, phi)

# Map spherical coordinates to Cartesian for plotting
x = np.sin(theta) * np.cos(phi)
y = np.sin(theta) * np.sin(phi)
z = np.cos(theta)

# Create the 3D surface plot
fig = go.Figure(data=[go.Surface(
    x=x, y=y, z=z,
    surfacecolor=scalar_field.real,  # Use the scalar field as color
    colorscale='Viridis',  # Choose a colormap
    colorbar_title='Value'
)])

fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z',
        aspectmode='data'  # Equal aspect ratio
    )
)

fig.show()

In [219]:
index = 0
for l in range(l_max):
    for m in range(-l, l + 1):
        index += 1
        
print(index)

100


## I'll take that as a proof of principle
It should be possiblet to use SH to upsample, in addition to regularizing. 

Now, let's step back and look at some summary stats

### Number of deep cells over time (in 1 half of embryo)

In [134]:
n_cell_vec = np.sum(face_df.loc[:, f_cols].to_numpy(), axis=1)

fig = px.scatter(x=time_vec, y=n_cell_vec)
fig.show()

### Deep cell velocity over time

In [1]:
# calculate average velocity and volume
deep_tracks_df[["dx", "dy", "dz"]] = deep_tracks_df.loc[:, ["track_id", "x", "y", "z"]].groupby(["track_id"]).diff()
deep_tracks_df["v"] = np.sqrt(deep_tracks_df["dx"]**2 + deep_tracks_df["dy"]**2 + deep_tracks_df["dz"]**2)

deep_tracks_v = deep_tracks_df.loc[:, ["t", "v"]].groupby(["t"]).mean().reset_index()

fig = px.scatter(deep_tracks_v, x="t", y="v", opacity=0.5, trendline="ewm", trendline_options=dict(halflife=15))
fig.update_layout(
    yaxis=dict(range=[0, 4])  # Set the y-axis range (min, max)
)
fig.show()

NameError: name 'deep_tracks_df' is not defined

### Entropy over time

In [209]:
# for this, I want SH interpolation
import flowshape as fs
import igl
import scipy as sp

l_max = 7 # this sets level of detail

v, f = sphere_mesh.vertices.copy(), sphere_mesh.faces.copy()
# this utility does the above steps + SH decomposition
# Here, using maximum degree 24

v_sphere = fs.sphere_map(v, f)
v_bary = igl.barycenter(v_sphere, f)
v_bary = fs.project_sphere(v_bary)
W = 0.5 * igl.doublearea(v_sphere, f)
W = sp.sparse.diags(W)

face_df_sh = face_df.copy()

for i in tqdm(range(face_df.shape[0])):

    face_intensity = face_df.loc[i, f_cols].to_numpy().ravel()
    mu = np.mean(face_intensity.copy())
    face_intensity_norm = face_intensity.copy() - mu
    
    weights, Y_mat = fs.IRF_scalar(face_intensity_norm, v_bary, W, max_degree=l_max)
    
    fi_recon = Y_mat.dot(weights) + mu
    fi_recon = fi_recon - np.min(fi_recon)#[fi_recon<0] = 1e-12
    face_df_sh.loc[i, f_cols] = fi_recon

100%|██████████| 1600/1600 [01:09<00:00, 23.06it/s]


In [211]:
fi_array = face_df_sh.loc[:, face_nz_cols].to_numpy().copy()
pdf_array = np.divide(fi_array, np.sum(fi_array, axis=1)[:, None])
entropy = -np.sum(np.multiply(pdf_array, np.log(pdf_array + 1e-12)), axis=1)

In [212]:
entropy

array([4.35798978, 4.35471801, 4.36635066, ..., 4.16825214, 4.1554241 ,
       4.14788697])

In [213]:
fig = px.scatter(x=time_vec, y=entropy)
fig.show()

In [173]:
entropy

0      -0.0
1      -0.0
2      -0.0
3      -0.0
4      -0.0
       ... 
1595   -0.0
1596   -0.0
1597   -0.0
1598   -0.0
1599   -0.0
Length: 1600, dtype: float64